## 15. Réfléchir à un autre type de réseau afin de résoudre ce problème

**=> Réseau Antagoniste Génératif (GAN)**
Les GAN sont composés de deux réseaux : un générateur qui crée des échantillons à partir de bruit, et un discriminateur qui apprend à distinguer les échantillons générés de ceux réels. Dans le contexte de la musique, un GAN pourrait générer de nouvelles séquences de notes en modifiant le générateur pour produire des séquences MIDI plausibles.

- Architecture :

  * Le générateur prendrait une séquence de bruit et produirait une séquence de notes et de durées.
  * Le discriminateur prendrait une séquence (notes et durées) et apprendrait à distinguer les séquences réelles (provenant du dataset) des séquences générées.

- Avantages :

  * Capacité à capturer des motifs complexes grâce à l'interaction compétitive entre le générateur et le discriminateur.
  * Potentiel de produire des séquences réalistes même sans supervision stricte sur la structure musicale.

- Inconvénients :

  * La formation des GAN est notoirement instable, ce qui pourrait entraîner des difficultés à générer des séquences de haute qualité.
  * Complexité plus élevée pour ajuster le modèle à la polyphonie et aux variations de tempo.


## 16. Bonus 1 : implémenter le réseau décrit à la question précédente.

In [16]:
import os
import numpy as np
import pretty_midi
import tensorflow as tf
from tensorflow.keras.layers import Dense, LSTM, Reshape, Conv1D, Flatten
from tensorflow.keras.models import Sequential
import IPython.display as ipd
import soundfile as sf

# Configuration de base
sequence_size = 100  # Nombre de notes par séquence
vocab_size = 128  # Ajusté pour couvrir la gamme de notes
latent_dim = 100  # Dimension de l'espace latent pour le générateur
batch_size = 16
epochs = 100

In [17]:

#* Charger les séquences
notes_sequences = np.load("notes_sequences.npy")
durations_sequences = np.load("durations_sequences.npy")

# Convertir les durées en entiers (discrétisation)
durations_sequences = tf.cast(durations_sequences * 100, tf.int32)  # *100 = pas de décimales

#* Convertir en tenseurs utilisables par Tensoflow
notes_sequences = tf.convert_to_tensor(notes_sequences, dtype=tf.int32)
durations_sequences = tf.convert_to_tensor(durations_sequences, dtype=tf.float32)

In [18]:
# Création des jeux d'entraînement pour le GAN
x_notes, y_notes = notes_sequences[:, :-1], notes_sequences[:, 1:] 
x_durations, y_durations = durations_sequences[:, :-1], durations_sequences[:, 1:]

In [19]:
# 2. Modèles de générateur et de discriminateur
    
def build_generator(latent_dim, sequence_size, vocab_size):
    model = Sequential()
    reshape_dim = sequence_size * 1
    
    # Couches communes
    input_layer = tf.keras.Input(shape=(latent_dim,))
    x = Dense(reshape_dim, activation='relu')(input_layer)
    x = Reshape((sequence_size, 1))(x)
    x = Conv1D(64, kernel_size=3, padding="same", activation="relu")(x)
    x = LSTM(128, return_sequences=True)(x)
    
    # Branche pour les notes
    notes_output = Dense(vocab_size, activation="softmax", name="notes")(x)
    
    # Branche pour les durées
    durations_output = Dense(vocab_size, activation="softmax", name="durations")(x)
    
    return tf.keras.Model(input_layer, [notes_output, durations_output])

In [20]:
def build_discriminator(sequence_size, vocab_size):
# Entrée pour les notes
    notes_input = tf.keras.Input(shape=(sequence_size, vocab_size))
    # Entrée pour les durées
    durations_input = tf.keras.Input(shape=(sequence_size, vocab_size))
    
    # Traitement des notes
    x_notes = Conv1D(64, kernel_size=3, padding="same")(notes_input)
    x_notes = LSTM(128, return_sequences=True)(x_notes)
    
    # Traitement des durées
    x_durations = Conv1D(64, kernel_size=3, padding="same")(durations_input)
    x_durations = LSTM(128, return_sequences=True)(x_durations)
    
    # Fusion des caractéristiques
    combined = tf.keras.layers.Concatenate()([x_notes, x_durations])
    x = Flatten()(combined)
    x = Dense(64, activation="relu")(x)
    output = Dense(1, activation="sigmoid")(x)
    
    return tf.keras.Model([notes_input, durations_input], output)

In [21]:
# 1. First compile the discriminator separately
discriminator = build_discriminator(sequence_size, vocab_size)
discriminator.compile(optimizer="adam", loss="binary_crossentropy", metrics=["accuracy"])

generator = build_generator(latent_dim, sequence_size, vocab_size)

def build_gan(generator, discriminator):
    discriminator.trainable = False # Freeze discriminator weights when training generator
    
    gan_input = tf.keras.Input(shape=(latent_dim,))
    generated_notes, generated_durations = generator(gan_input)
    # Generate notes using the generator
    gan_output = discriminator([generated_notes, generated_durations])
    
    # Create and compile GAN
    gan = tf.keras.Model(gan_input, gan_output)
    gan.compile(optimizer="adam", loss="binary_crossentropy")
    return gan

gan = build_gan(generator, discriminator)


In [24]:
# 3. Entraînement du GAN
# Boucle d'entraînement
for epoch in range(epochs):
    noise = np.random.normal(0, 1, (batch_size, latent_dim))
    
    generated_notes, generated_durations = generator.predict(noise)
    
    idx = tf.random.uniform([batch_size], 0, x_notes.shape[0], dtype=tf.int32)
    real_notes = tf.gather(x_notes, idx)
    real_durations = tf.gather(x_durations, idx)
    
    # One-hot encoding avec les durées converties en entiers
    real_notes = tf.one_hot(real_notes, vocab_size)
    real_durations = tf.one_hot(tf.cast(real_durations, tf.int32), vocab_size)
    
    # Entraîner le discriminateur
    discriminator.trainable = True
    d_loss_real = discriminator.train_on_batch(
        [real_notes, real_durations], 
        np.ones((batch_size, 1))
    )
    d_loss_fake = discriminator.train_on_batch(
        [generated_notes, generated_durations], 
        np.zeros((batch_size, 1))
    )
    
    # Entraîner le générateur
    discriminator.trainable = False
    g_loss = gan.train_on_batch(
        noise, 
        np.ones((batch_size, 1))
    )
    
    if epoch % 1000 == 0:
        print(f"Epoch {epoch}, D Loss Real: {d_loss_real}, D Loss Fake: {d_loss_fake}, G Loss: {g_loss}")

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 111ms/step
Epoch 0, D Loss Real: [array(0.72593707, dtype=float32), array(0., dtype=float32)], D Loss Fake: [array(0.72863567, dtype=float32), array(0., dtype=float32)], G Loss: [array(0.72863567, dtype=float32), array(0.72863567, dtype=float32), array(0., dtype=float32)]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 62ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 61ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 57ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━

In [25]:
# Sauvegarde du générateur
generator.save("03-gan_generator.h5")

In [26]:
# 4. Génération de nouveaux morceaux
def generate_music(generator, latent_dim, num_notes=100, output_path="generated_music.mid"):
    noise = np.random.normal(0, 1, (1, latent_dim))
    generated_sequence = generator.predict(noise)
    generated_notes = tf.argmax(generated_sequence, axis=-1).numpy().flatten()

    # Création du fichier MIDI
    midi_data = pretty_midi.PrettyMIDI()
    instrument = pretty_midi.Instrument(program=0)  # Piano par défaut
    current_time = 0  # Temps de démarrage pour la première note
    
    for pitch in generated_notes[:num_notes]:
        note = pretty_midi.Note(
            velocity=100,
            pitch=int(pitch),
            start=current_time,
            end=current_time + 0.5  # Durée fixe de 0.5 pour simplification
        )
        instrument.notes.append(note)
        current_time += 0.5
    
    midi_data.instruments.append(instrument)
    midi_data.write(output_path)
    print(f"Morceau généré et sauvegardé sous {output_path}")

# Générer un morceau
generate_music(generator, latent_dim, num_notes=100, output_path="generated_midis/03-gan.mid")


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 469ms/step
Morceau généré et sauvegardé sous generated_midis/03-gan.mid


In [27]:
output_file = "./generated_midis/03-gan.mid"
midi_data = pretty_midi.PrettyMIDI(output_file)

audio_file = "./generated_midis/03-gan.wav"
waveform = midi_data.synthesize()
sf.write(audio_file, waveform, samplerate=44100)

ipd.Audio(audio_file)